### Process of Running GeoTopic Parser:

1. Navigate to directory /Tika_GeoTopic_Parser and run command to start lucene server:
    ```bash
    lucene-geo-gazetteer -server
    ```
    - If the server is running, you should see this: 
        ```bash
        INFO: Starting ProtocolHandler ["http-nio-8765"]
        ```
2. In new terminal, navigate to directory /Tika_GeoTopic_Parser and run command to start geotopic server: 
     ```bash
    ./geotopic-server
    ```
    - If the server is running, you should see this: 
        ```bash
        INFO  [main] 16:25:04,222 org.apache.tika.server.core.TikaServerProcess Started Apache Tika server ff835cb6-9aa1-4817-ba8d-d035eb174c87 at http://localhost:9998/
        ```

3. In new terminal, navigate to directory /Tika_GeoTopic_Parser and run command to test servers: 
    ```bash
        java -cp \
        "tika-build/tika-app-2.7.0.jar:tika-build/tika-parser-nlp-package-2.7.0.jar:./location-ner-model:./geotopic-mime" \
        -Dorg.apache.tika.mime.custom-mimetypes=geotopic-mime/org/apache/tika/mime/custom-mimetypes.xml \
        org.apache.tika.cli.TikaCLI \ -m polar.geot
    ```
    - If command is running correctly, the output should be: 
        ```bash
        United States, 39.76, -98.5    
        ```



In [12]:
import os
from tika import parser
import re
import pandas as pd
import requests

In [13]:
directory_path = '../../Tika_GeoTopic_Parser/Haunted_Places_Text_Files'
tsv_path = '../../data/haunted_places_entities.tsv'
output_path = '../../data/haunted_places_location.tsv'
gazetteer_url = "http://localhost:8765/api/search"

In [14]:
df_master_dataset = pd.read_csv(tsv_path, sep='\t', engine='python')
df_master_dataset

city        country  \
0                Ada  United States   
1            Addison  United States   
2             Adrian  United States   
3             Adrian  United States   
4             Albion  United States   
...              ...            ...   
10987    Westminster  United States   
10988    Westminster  United States   
10989    Wheat Ridge  United States   
10990    Wheat Ridge  United States   
10991  Woodland Park  United States   

                                             description  \
0      Ada witch - Sometimes you can see a misty blue...   
1      A little girl was killed suddenly while waitin...   
2      If you take Gorman Rd. west towards Sand Creek...   
3      In the 1970's, one room, room 211, in the old ...   
4      Kappa Delta Sorority - The Kappa Delta Sororit...   
...                                                  ...   
10987  at 12 midnight you can see a lady with two lit...   
10988  Is haunted by the victims of a murder that hap...   
10989  The institution was for kids 18 years old and ...   
10990  Gymnasium -  their have been reports of a litt...   
10991  Cadets from the Air Force Academy participatin...   

                        location     state state_abbrev   longitude  \
0                   Ada Cemetery  Michigan           MI  -85.504893   
1                North Adams Rd.  Michigan           MI  -84.381843   
2                  Ghost Trestle  Michigan           MI  -84.035656   
3       Siena Heights University  Michigan           MI  -84.017565   
4                 Albion College  Michigan           MI  -84.745177   
...                          ...       ...          ...         ...   
10987                  city hall  Colorado           CO -105.048936   
10988             Pillar of Fire  Colorado           CO -105.032091   
10989   Ridge Mental Institution  Colorado           CO -105.063974   
10990  Wheat Ridge Middle School  Colorado           CO -105.103613   
10991         Saylor Park Forest  Colorado           CO -105.022763   

        latitude  city_longitude  city_latitude  \
0      42.962106      -85.495480      42.960727   
1      41.971425      -84.347168      41.986434   
2      41.904538      -84.037166      41.897547   
3      41.905712      -84.037166      41.897547   
4      42.244006      -84.753030      42.243097   
...          ...             ...            ...   
10987  39.862610     -105.037205      39.836653   
10988  39.847237     -105.037205      39.836653   
10989  39.769726     -105.077206      39.766098   
10990  39.764055     -105.077206      39.766098   
10991  39.116658     -105.056930      38.993881   

                                           Entity Labels  \
0      ['ORG', 'QUANTITY', 'FAC', 'ORG', 'GPE', 'TIME...   
1                                       ['DATE', 'DATE']   
2      ['FAC', 'GPE', 'CARDINAL', 'CARDINAL', 'TIME',...   
3      ['DATE', 'CARDINAL', 'CARDINAL', 'DATE', 'CARD...   
4                                    ['ORG', 'CARDINAL']   
...                                                  ...   
10987                     ['TIME', 'CARDINAL', 'PERSON']   
10988                                           ['DATE']   
10989           ['DATE', 'DATE', 'CARDINAL', 'CARDINAL']   
10990                                                NaN   
10991                             ['ORG', 'GPE', 'DATE']   

                                            Entity Texts  
0      ['Ada witch -', '3-mile', 'the Ada Cemetery', ...  
1                       ['in.1 month later', 'this day']  
2      ['Gorman Rd', 'Sand Creek', 'one', 'one', 'Lat...  
3      ['1970', 'one', '211', 'today', 'one', 'two', ...  
4      ['Kappa Delta Sorority - The Kappa Delta Soror...  
...                                                  ...  
10987             ['12 midnight', 'two', 'Sheridan St.']  
10988                                      ['years ago']  
10989          ['18 years old', '70', 'one', 'hundreds']  
10990                                            

In [15]:
cnt = 0
directory = sorted(os.listdir(directory_path))

for file in directory:
    if not file.endswith(".txt"):
        continue

    cnt += 1
    try:
        index = int(file.rsplit('_', 1)[-1].split('.')[0])
    except ValueError:
        print(f"[!] Skipping invalid file: {file}")
        continue

    file_path = os.path.join(directory_path, file)

    # Step 1: Extract location
    location = None
    with open(file_path, "r", encoding="utf-8") as f:
        for line in f:
            match = re.search(r"^Location:\s*(.+)$", line, re.IGNORECASE)
            if match:
                location = match.group(1).strip()
                break

    print(f"[DEBUG] {file} → Extracted location: {location}")

    name = lat = lon = "NaN"

    # Step 2: Query Gazetteer
    if location:
        try:
            response = requests.get(gazetteer_url, params={"s": location})
            print(f"[DEBUG] Query: {response.url}")
            print(f"[DEBUG] Status: {response.status_code}")
            print(f"[DEBUG] Response: {response.text}")

            if response.status_code == 200:
                results = response.json()
                matched_key = next((k for k in results if k.lower() == location.lower()), None)

                if matched_key and results[matched_key]:
                    top_place = results[matched_key][0]
                    name = top_place.get("name", matched_key)
                    lat = top_place.get("latitude", "NaN")
                    lon = top_place.get("longitude", "NaN")
                else:
                    # Fallback: Try "Location County"
                    location_alt = f"{location} County"
                    response = requests.get(gazetteer_url, params={"s": location_alt})
                    results = response.json()
                    matched_key = next((k for k in results if k.lower() == location_alt.lower()), None)
                    if matched_key and results[matched_key]:
                        top_place = results[matched_key][0]
                        name = top_place.get("name", matched_key)
                        lat = top_place.get("latitude", "NaN")
                        lon = top_place.get("longitude", "NaN")

        except Exception as e:
            print(f"[X] {file} → Failed to resolve {location}: {e}")

    # Step 3: Save to DataFrame
    df_master_dataset.loc[index, 'GeoTopic Name'] = name
    df_master_dataset.loc[index, 'GeoTopic Latitude'] = lat
    df_master_dataset.loc[index, 'GeoTopic Longitude'] = lon

    print(f"Processed file {cnt}: {file} - ({name}, {lat}, {lon})")

[DEBUG] Haunted_Places_0.txt → Extracted location: Ada Cemetery
[DEBUG] Query: http://localhost:8765/api/search?s=Ada+Cemetery
[DEBUG] Status: 200
[DEBUG] Response: {"Ada Cemetery":[{"name":"Ada Cemetery","countryCode":"US","admin1Code":"MI","admin2Code":"081","latitude":42.96252,"longitude":-85.50474}]}

Processed file 1: Haunted_Places_0.txt - (Ada Cemetery, 42.96252, -85.50474)
[DEBUG] Haunted_Places_1.txt → Extracted location: North Adams Rd.
[DEBUG] Query: http://localhost:8765/api/search?s=North+Adams+Rd.
[DEBUG] Status: 200
[DEBUG] Response: {}

Processed file 2: Haunted_Places_1.txt - (NaN, NaN, NaN)
[DEBUG] Haunted_Places_10.txt → Extracted location: The Yellow Motel
[DEBUG] Query: http://localhost:8765/api/search?s=The+Yellow+Motel
[DEBUG] Status: 200
[DEBUG] Response: {}

Processed file 3: Haunted_Places_10.txt - (NaN, NaN, NaN)
[DEBUG] Haunted_Places_100.txt → Extracted location: O.W. Best Middle School
[DEBUG] Query: http://localhost:8765/api/search?s=O.W.+Best+Middle+Scho

/var/folders/76/p5qc7ncx17x4_grc1k0mw0880000gn/T/ipykernel_3717/2631749194.py:64: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value 'NaN' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df_master_dataset.loc[index, 'GeoTopic Latitude'] = lat
/var/folders/76/p5qc7ncx17x4_grc1k0mw0880000gn/T/ipykernel_3717/2631749194.py:65: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value 'NaN' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df_master_dataset.loc[index, 'GeoTopic Longitude'] = lon


[DEBUG] Haunted_Places_10012.txt → Extracted location: The St. Joseph School District offices
[DEBUG] Query: http://localhost:8765/api/search?s=The+St.+Joseph+School+District+offices
[DEBUG] Status: 200
[DEBUG] Response: {}

Processed file 19: Haunted_Places_10012.txt - (NaN, NaN, NaN)
[DEBUG] Haunted_Places_10013.txt → Extracted location: The Social Parlor
[DEBUG] Query: http://localhost:8765/api/search?s=The+Social+Parlor
[DEBUG] Status: 200
[DEBUG] Response: {}

Processed file 20: Haunted_Places_10013.txt - (NaN, NaN, NaN)
[DEBUG] Haunted_Places_10014.txt → Extracted location: Alexian Brothers Hospital Site
[DEBUG] Query: http://localhost:8765/api/search?s=Alexian+Brothers+Hospital+Site
[DEBUG] Status: 200
[DEBUG] Response: {}

Processed file 21: Haunted_Places_10014.txt - (NaN, NaN, NaN)
[DEBUG] Haunted_Places_10015.txt → Extracted location: The Book House
[DEBUG] Query: http://localhost:8765/api/search?s=The+Book+House
[DEBUG] Status: 200
[DEBUG] Response: {}

Processed file 22: H

In [16]:
# Step 4: Save output to TSV
df_master_dataset.to_csv(output_path, sep="\t", index=False, encoding="utf-8")
print(f"\n Saved updated dataset to: {output_path}")



 Saved updated dataset to: ../../data/haunted_places_location.tsv


In [10]:
df_new = pd.read_csv(output_path, sep='\t', engine='python')
df_new

city        country  \
0                Ada  United States   
1            Addison  United States   
2             Adrian  United States   
3             Adrian  United States   
4             Albion  United States   
...              ...            ...   
10987    Westminster  United States   
10988    Westminster  United States   
10989    Wheat Ridge  United States   
10990    Wheat Ridge  United States   
10991  Woodland Park  United States   

                                             description  \
0      Ada witch - Sometimes you can see a misty blue...   
1      A little girl was killed suddenly while waitin...   
2      If you take Gorman Rd. west towards Sand Creek...   
3      In the 1970's, one room, room 211, in the old ...   
4      Kappa Delta Sorority - The Kappa Delta Sororit...   
...                                                  ...   
10987  at 12 midnight you can see a lady with two lit...   
10988  Is haunted by the victims of a murder that hap...   
10989  The institution was for kids 18 years old and ...   
10990  Gymnasium -  their have been reports of a litt...   
10991  Cadets from the Air Force Academy participatin...   

                        location     state state_abbrev   longitude  \
0                   Ada Cemetery  Michigan           MI  -85.504893   
1                North Adams Rd.  Michigan           MI  -84.381843   
2                  Ghost Trestle  Michigan           MI  -84.035656   
3       Siena Heights University  Michigan           MI  -84.017565   
4                 Albion College  Michigan           MI  -84.745177   
...                          ...       ...          ...         ...   
10987                  city hall  Colorado           CO -105.048936   
10988             Pillar of Fire  Colorado           CO -105.032091   
10989   Ridge Mental Institution  Colorado           CO -105.063974   
10990  Wheat Ridge Middle School  Colorado           CO -105.103613   
10991         Saylor Park Forest  Colorado           CO -105.022763   

        latitude  city_longitude  city_latitude  \
0      42.962106      -85.495480      42.960727   
1      41.971425      -84.347168      41.986434   
2      41.904538      -84.037166      41.897547   
3      41.905712      -84.037166      41.897547   
4      42.244006      -84.753030      42.243097   
...          ...             ...            ...   
10987  39.862610     -105.037205      39.836653   
10988  39.847237     -105.037205      39.836653   
10989  39.769726     -105.077206      39.766098   
10990  39.764055     -105.077206      39.766098   
10991  39.116658     -105.056930      38.993881   

                                           Entity Labels  \
0      ['ORG', 'QUANTITY', 'FAC', 'ORG', 'GPE', 'TIME...   
1                                       ['DATE', 'DATE']   
2      ['FAC', 'GPE', 'CARDINAL', 'CARDINAL', 'TIME',...   
3      ['DATE', 'CARDINAL', 'CARDINAL', 'DATE', 'CARD...   
4                                    ['ORG', 'CARDINAL']   
...                                                  ...   
10987                     ['TIME', 'CARDINAL', 'PERSON']   
10988                                           ['DATE']   
10989           ['DATE', 'DATE', 'CARDINAL', 'CARDINAL']   
10990                                                NaN   
10991                             ['ORG', 'GPE', 'DATE']   

                                            Entity Texts  \
0      ['Ada witch -', '3-mile', 'the Ada Cemetery', ...   
1                       ['in.1 month later', 'this day']   
2      ['Gorman Rd', 'Sand Creek', 'one', 'one', 'Lat...   
3      ['1970', 'one', '211', 'today', 'one', 'two', ...   
4      ['Kappa Delta Sorority - The Kappa Delta Soror...   
...                                                  ...   
10987             ['12 midnight', 'two', 'Sheridan St.']   
10988                                      ['years ago']   
10989          ['18 years old', '70', 'one', 'hundreds']   
10990                                  

In [17]:
# Total entries
total_entries = len(df_new)

# Count valid (non-NaN) lat/lon rows
known_count = (~df_new["GeoTopic Latitude"].isna() & ~df_new["GeoTopic Longitude"].isna()).sum()
unknown_count = total_entries - known_count

# Calculate percentages
known_percentage = (known_count / total_entries) * 100
unknown_percentage = (unknown_count / total_entries) * 100

# Print results
print(f"Entries with valid coordinates: {known_count} ({known_percentage:.2f}%)")
print(f"Entries with NaN coordinates: {unknown_count} ({unknown_percentage:.2f}%)")


Entries with valid coordinates: 3912 (35.59%)
Entries with NaN coordinates: 7080 (64.41%)
